In [2]:
#imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import folium as fm
from folium.plugins import HeatMap
from folium.plugins import HeatMapWithTime
from branca.element import Figure
from folium.plugins import DualMap


In [4]:
#mount google drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [5]:
#read the file from the team google drive foler
data = pd.read_csv("/content/drive/My Drive/Motor_Vehicle_Collisions_-_Crashes.csv")

/tmp/ipython-input-166129919.py:2: DtypeWarning: Columns (3) have mixed types. Specify dtype option on import or set low_memory=False.
  data = pd.read_csv("/content/drive/My Drive/Motor_Vehicle_Collisions_-_Crashes.csv")


In [6]:
#view column names
print(data.columns.tolist)

<bound method IndexOpsMixin.tolist of Index(['CRASH DATE', 'CRASH TIME', 'BOROUGH', 'ZIP CODE', 'LATITUDE',
       'LONGITUDE', 'LOCATION', 'ON STREET NAME', 'CROSS STREET NAME',
       'OFF STREET NAME', 'NUMBER OF PERSONS INJURED',
       'NUMBER OF PERSONS KILLED', 'NUMBER OF PEDESTRIANS INJURED',
       'NUMBER OF PEDESTRIANS KILLED', 'NUMBER OF CYCLIST INJURED',
       'NUMBER OF CYCLIST KILLED', 'NUMBER OF MOTORIST INJURED',
       'NUMBER OF MOTORIST KILLED', 'CONTRIBUTING FACTOR VEHICLE 1',
       'CONTRIBUTING FACTOR VEHICLE 2', 'CONTRIBUTING FACTOR VEHICLE 3',
       'CONTRIBUTING FACTOR VEHICLE 4', 'CONTRIBUTING FACTOR VEHICLE 5',
       'COLLISION_ID', 'VEHICLE TYPE CODE 1', 'VEHICLE TYPE CODE 2',
       'VEHICLE TYPE CODE 3', 'VEHICLE TYPE CODE 4', 'VEHICLE TYPE CODE 5'],
      dtype='object')>


In [7]:
#total nan values
total_nans = data.isna().sum()
print(total_nans)

CRASH DATE                             0
CRASH TIME                             0
BOROUGH                           678888
ZIP CODE                          679163
LATITUDE                          240297
LONGITUDE                         240297
LOCATION                          240297
ON STREET NAME                    481566
CROSS STREET NAME                 845697
OFF STREET NAME                  1824364
NUMBER OF PERSONS INJURED             18
NUMBER OF PERSONS KILLED              31
NUMBER OF PEDESTRIANS INJURED          0
NUMBER OF PEDESTRIANS KILLED           0
NUMBER OF CYCLIST INJURED              0
NUMBER OF CYCLIST KILLED               0
NUMBER OF MOTORIST INJURED             0
NUMBER OF MOTORIST KILLED              0
CONTRIBUTING FACTOR VEHICLE 1       7798
CONTRIBUTING FACTOR VEHICLE 2     354731
CONTRIBUTING FACTOR VEHICLE 3    2053404
CONTRIBUTING FACTOR VEHICLE 4    2176998
CONTRIBUTING FACTOR VEHICLE 5    2203542
COLLISION_ID                           0
VEHICLE TYPE COD

In [9]:
#head
data.head()

CRASH DATE CRASH TIME   BOROUGH ZIP CODE  LATITUDE  LONGITUDE  \
0  09/11/2021       2:39       NaN      NaN       NaN        NaN   
1  03/26/2022      11:45       NaN      NaN       NaN        NaN   
2  11/01/2023       1:29  BROOKLYN  11230.0  40.62179 -73.970024   
3  06/29/2022       6:55       NaN      NaN       NaN        NaN   
4  09/21/2022      13:21       NaN      NaN       NaN        NaN   

                 LOCATION           ON STREET NAME CROSS STREET NAME  \
0                     NaN    WHITESTONE EXPRESSWAY         20 AVENUE   
1                     NaN  QUEENSBORO BRIDGE UPPER               NaN   
2  (40.62179, -73.970024)            OCEAN PARKWAY          AVENUE K   
3                     NaN       THROGS NECK BRIDGE               NaN   
4                     NaN          BROOKLYN BRIDGE               NaN   

  OFF STREET NAME  ...  CONTRIBUTING FACTOR VEHICLE 2  \
0             NaN  ...                    Unspecified   
1             NaN  ...                            NaN   
2             NaN  ...                    Unspecified   
3             NaN  ...                    Unspecified   
4             NaN  ...                    Unspecified   

   CONTRIBUTING FACTOR VEHICLE 3  CONTRIBUTING FACTOR VEHICLE 4  \
0                            NaN                            NaN   
1                            NaN                            NaN   
2                    Unspecified                            NaN   
3                            NaN                            NaN   
4                            NaN                            NaN   

   CONTRIBUTING FACTOR VEHICLE 5  COLLISION_ID  \
0                            NaN       4455765   
1                            NaN       4513547   
2                            NaN       4675373   
3                            NaN       4541903   
4                            NaN       4566131   

                   VEHICLE TYPE CODE 1  VEHICLE TYPE CODE 2  \
0                                Sedan                Sedan   
1                                Sedan                  NaN   
2                                Moped                Sedan   
3                                Sedan        Pick-up Truck   
4  Station Wagon/Sport Utility Vehicle                  NaN   

   VEHICLE TYPE CODE 3 VEHICLE TYPE CODE 4 VEHICLE TYPE CODE 5  
0                  NaN                 NaN                 NaN  
1                  NaN                 NaN                 NaN  
2                Sedan                 NaN                 NaN  
3                  NaN                 NaN                 NaN  
4                  NaN                 NaN                 NaN  

[5 rows x 29 columns]

In [10]:
#thats a lot of lines
data.shape

(2213556, 29)

In [11]:
#drop a few columns because about 2 million nans
data = data.drop(columns = ["OFF STREET NAME","CONTRIBUTING FACTOR VEHICLE 3","CONTRIBUTING FACTOR VEHICLE 4","CONTRIBUTING FACTOR VEHICLE 5","VEHICLE TYPE CODE 3","VEHICLE TYPE CODE 4","VEHICLE TYPE CODE 5"])

In [12]:
#new head showing missing columns
data.head()

CRASH DATE CRASH TIME   BOROUGH ZIP CODE  LATITUDE  LONGITUDE  \
0  09/11/2021       2:39       NaN      NaN       NaN        NaN   
1  03/26/2022      11:45       NaN      NaN       NaN        NaN   
2  11/01/2023       1:29  BROOKLYN  11230.0  40.62179 -73.970024   
3  06/29/2022       6:55       NaN      NaN       NaN        NaN   
4  09/21/2022      13:21       NaN      NaN       NaN        NaN   

                 LOCATION           ON STREET NAME CROSS STREET NAME  \
0                     NaN    WHITESTONE EXPRESSWAY         20 AVENUE   
1                     NaN  QUEENSBORO BRIDGE UPPER               NaN   
2  (40.62179, -73.970024)            OCEAN PARKWAY          AVENUE K   
3                     NaN       THROGS NECK BRIDGE               NaN   
4                     NaN          BROOKLYN BRIDGE               NaN   

   NUMBER OF PERSONS INJURED  ...  NUMBER OF PEDESTRIANS KILLED  \
0                        2.0  ...                             0   
1                        1.0  ...                             0   
2                        1.0  ...                             0   
3                        0.0  ...                             0   
4                        0.0  ...                             0   

   NUMBER OF CYCLIST INJURED  NUMBER OF CYCLIST KILLED  \
0                          0                         0   
1                          0                         0   
2                          0                         0   
3                          0                         0   
4                          0                         0   

   NUMBER OF MOTORIST INJURED  NUMBER OF MOTORIST KILLED  \
0                           2                          0   
1                           1                          0   
2                           1                          0   
3                           0                          0   
4                           0                          0   

   CONTRIBUTING FACTOR VEHICLE 1  CONTRIBUTING FACTOR VEHICLE 2 COLLISION_ID  \
0   Aggressive Driving/Road Rage                    Unspecified      4455765   
1              Pavement Slippery                            NaN      4513547   
2                    Unspecified                    Unspecified      4675373   
3          Following Too Closely                    Unspecified      4541903   
4            Passing Too Closely                    Unspecified      4566131   

                   VEHICLE TYPE CODE 1  VEHICLE TYPE CODE 2  
0                                Sedan                Sedan  
1                                Sedan                  NaN  
2                                Moped                Sedan  
3                                Sedan        Pick-up Truck  
4  Station Wagon/Sport Utility Vehicle                  NaN  

[5 rows x 22 columns]

In [13]:
#new shape
data.shape

(2213556, 22)

In [14]:
#rerun total nans
total_nans = data.isna().sum()
print(total_nans)

CRASH DATE                            0
CRASH TIME                            0
BOROUGH                          678888
ZIP CODE                         679163
LATITUDE                         240297
LONGITUDE                        240297
LOCATION                         240297
ON STREET NAME                   481566
CROSS STREET NAME                845697
NUMBER OF PERSONS INJURED            18
NUMBER OF PERSONS KILLED             31
NUMBER OF PEDESTRIANS INJURED         0
NUMBER OF PEDESTRIANS KILLED          0
NUMBER OF CYCLIST INJURED             0
NUMBER OF CYCLIST KILLED              0
NUMBER OF MOTORIST INJURED            0
NUMBER OF MOTORIST KILLED             0
CONTRIBUTING FACTOR VEHICLE 1      7798
CONTRIBUTING FACTOR VEHICLE 2    354731
COLLISION_ID                          0
VEHICLE TYPE CODE 1               16030
VEHICLE TYPE CODE 2              442979
dtype: int64


In [15]:
#dropping all nans to see what is left over
new_data = data.dropna()#subset=["CROSS STREET NAME"])
new_data.shape

(934714, 22)

In [16]:
#we were able to save 934714 rows for our data
no_nans = new_data.isna().sum()
print(no_nans)

CRASH DATE                       0
CRASH TIME                       0
BOROUGH                          0
ZIP CODE                         0
LATITUDE                         0
LONGITUDE                        0
LOCATION                         0
ON STREET NAME                   0
CROSS STREET NAME                0
NUMBER OF PERSONS INJURED        0
NUMBER OF PERSONS KILLED         0
NUMBER OF PEDESTRIANS INJURED    0
NUMBER OF PEDESTRIANS KILLED     0
NUMBER OF CYCLIST INJURED        0
NUMBER OF CYCLIST KILLED         0
NUMBER OF MOTORIST INJURED       0
NUMBER OF MOTORIST KILLED        0
CONTRIBUTING FACTOR VEHICLE 1    0
CONTRIBUTING FACTOR VEHICLE 2    0
COLLISION_ID                     0
VEHICLE TYPE CODE 1              0
VEHICLE TYPE CODE 2              0
dtype: int64


In [17]:
#save new dataset localy
new_data.to_csv('output.csv', index=False)

In [18]:
new_data.describe()

LATITUDE      LONGITUDE  NUMBER OF PERSONS INJURED  \
count  934714.000000  934714.000000              934714.000000   
mean       40.660233     -73.811268                   0.300999   
std         1.578938       2.864037                   0.733865   
min         0.000000     -74.254960                   0.000000   
25%        40.666893     -73.977653                   0.000000   
50%        40.719048     -73.931265                   0.000000   
75%        40.764786     -73.871187                   0.000000   
max        40.912468       0.000000                  43.000000   

       NUMBER OF PERSONS KILLED  NUMBER OF PEDESTRIANS INJURED  \
count             934714.000000                  934714.000000   
mean                   0.000884                       0.003109   
std                    0.032368                       0.069269   
min                    0.000000                       0.000000   
25%                    0.000000                       0.000000   
50%                    0.000000                       0.000000   
75%                    0.000000                       0.000000   
max                    8.000000                      15.000000   

       NUMBER OF PEDESTRIANS KILLED  NUMBER OF CYCLIST INJURED  \
count                 934714.000000              934714.000000   
mean                       0.000163                   0.038353   
std                        0.014772                   0.194428   
min                        0.000000                   0.000000   
25%                        0.000000                   0.000000   
50%                        0.000000                   0.000000   
75%                        0.000000                   0.000000   
max                        6.000000                   4.000000   

       NUMBER OF CYCLIST KILLED  NUMBER OF MOTORIST INJURED  \
count             934714.000000               934714.000000   
mean                   0.000169                    0.254434   
std                    0.013082                    0.713670   
min                    0.000000                    0.000000   
25%                    0.000000                    0.000000   
50%                    0.000000                    0.000000   
75%                    0.000000                    0.000000   
max                    2.000000                   43.000000   

       NUMBER OF MOTORIST KILLED  COLLISION_ID  
count              934714.000000  9.347140e+05  
mean                    0.000522  2.660220e+06  
std                     0.024208  1.743058e+06  
min                     0.000000  2.200000e+01  
25%                     0.000000  3.114015e+05  
50%                     0.000000  3.346812e+06  
75%                     0.000000  4.042110e+06  
max                     3.000000  4.850344e+06

overall heatmap ny with locations where crashes occured

In [42]:

overall_hm = new_data[['LATITUDE','LONGITUDE']].values.tolist()
nyc_center = [40.7128, -74.0060]
omap = fm.Map(location=nyc_center, zoom_start=10)
HeatMap(overall_hm, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(omap)
omap
#omap.save("Overall_Crashes_Heatmap.html")

Output hidden; open in https://colab.research.google.com to view.

heatmaps of collision by burrough

In [20]:
bor_count = new_data['BOROUGH'].value_counts()
bor_count

BOROUGH
BROOKLYN         292149
QUEENS           258318
MANHATTAN        217962
BRONX            125273
STATEN ISLAND     41012
Name: count, dtype: int64

In [21]:
#MANHATTAN
man_data = new_data[new_data['BOROUGH'] == 'MANHATTAN']
overall_man = man_data[['LATITUDE','LONGITUDE']].values.tolist()
man_center = [40.7685, -73.9822]
manmap = fm.Map(location=man_center, zoom_start=10)
HeatMap(overall_man, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(manmap)
manmap
#manmap.save('Manhattan_Crashes_Heatmap.html')

Output hidden; open in https://colab.research.google.com to view.

In [22]:
#STATEN ISLAND
si_data = new_data[new_data['BOROUGH'] == 'STATEN ISLAND']
overall_si = si_data[['LATITUDE','LONGITUDE']].values.tolist()
si_center = [40.6132, -74.1214]
simap = fm.Map(location=si_center, zoom_start=10)
HeatMap(overall_si, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(simap)
simap
#simap.save('Staten_Island_Crashes_Heatmap.html')

In [23]:
#BROOKLYN
lyn_data = new_data[new_data['BOROUGH'] == 'BROOKLYN']
overall_lyn = lyn_data[['LATITUDE','LONGITUDE']].values.tolist()
lyn_center = [40.6782, -73.9442]
lynmap = fm.Map(location=lyn_center, zoom_start=10)
HeatMap(overall_lyn, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(lynmap)
lynmap
#lynmap.save('Brooklyn_Crashes_Heatmap.html')

Output hidden; open in https://colab.research.google.com to view.

In [24]:
#QUEENS
qz_data = new_data[new_data['BOROUGH'] == 'QUEENS']
overall_qz = qz_data[['LATITUDE','LONGITUDE']].values.tolist()
qz_center = [40.7282, -73.7949]
qzmap = fm.Map(location=qz_center, zoom_start=10)
HeatMap(overall_qz, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(qzmap)
qzmap
#qzmap.save('Queens_Crashes_Heatmap.html')

Output hidden; open in https://colab.research.google.com to view.

In [25]:
#BRONX
onx_data = new_data[new_data['BOROUGH'] == 'BRONX']
overall_onx = onx_data[['LATITUDE','LONGITUDE']].values.tolist()
onx_center = [40.8448, -73.8648]
onxmap = fm.Map(location=onx_center, zoom_start=10)
HeatMap(overall_onx, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(onxmap)
onxmap
#onxmap.save('Bronx_Crashes_Heatmap.html')

Output hidden; open in https://colab.research.google.com to view.

injuries / fatalities

In [29]:
bor_data = new_data[(new_data['NUMBER OF PERSONS KILLED'] > 0) | (new_data['NUMBER OF PERSONS INJURED'] > 0)]
tor_count = bor_data['BOROUGH'].value_counts()
tor_count

BOROUGH
BROOKLYN         70079
QUEENS           57332
MANHATTAN        29372
BRONX            28161
STATEN ISLAND     8401
Name: count, dtype: int64

In [30]:
fman = man_data[(man_data['NUMBER OF PERSONS KILLED'] > 0) | (man_data['NUMBER OF PERSONS INJURED'] > 0)]
foverall_man = fman[['LATITUDE','LONGITUDE']].values.tolist()
man_center = [40.7685, -73.9822]
fmanmap = fm.Map(location=man_center, zoom_start=10)
HeatMap(foverall_man, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(fmanmap)
fmanmap
#fmanmap.save('Manhattan_Injuries_Heatmap.html')

In [31]:
fsi = si_data[(si_data['NUMBER OF PERSONS KILLED'] > 0) | (si_data['NUMBER OF PERSONS INJURED'] > 0)]
foverall_si = fsi[['LATITUDE','LONGITUDE']].values.tolist()
si_center = [40.6132, -74.1214]
fsimap = fm.Map(location=si_center, zoom_start=10)
HeatMap(foverall_si, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(fsimap)
fsimap
#fsimap.save('Staten_Island_Injuries_Heatmap.html')

In [32]:
flyn = lyn_data[(lyn_data['NUMBER OF PERSONS KILLED'] > 0) | (lyn_data['NUMBER OF PERSONS INJURED'] > 0)]
foverall_lyn = flyn[['LATITUDE','LONGITUDE']].values.tolist()
lyn_center = [40.6782, -73.9442]
flynmap = fm.Map(location=lyn_center, zoom_start=10)
HeatMap(foverall_lyn, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(flynmap)
flynmap
#flynmap.save('Brooklyn_Injuries_Heatmap.html')

In [33]:
fqz = qz_data[(qz_data['NUMBER OF PERSONS KILLED'] > 0) | (qz_data['NUMBER OF PERSONS INJURED'] > 0)]
foverall_qz = fqz[['LATITUDE','LONGITUDE']].values.tolist()
qz_center = [40.7282, -73.7949]
fqzmap = fm.Map(location=qz_center, zoom_start=10)
HeatMap(foverall_qz, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(fqzmap)
fqzmap
#fqzmap.save('Queens_Injuries_Heatmap.html')

In [34]:
fonx = onx_data[(onx_data['NUMBER OF PERSONS KILLED'] > 0) | (onx_data['NUMBER OF PERSONS INJURED'] > 0)]
foverall_onx = fonx[['LATITUDE','LONGITUDE']].values.tolist()
onx_center = [40.8448, -73.8648]
fonxmap = fm.Map(location=onx_center, zoom_start=10)
HeatMap(foverall_onx, radius=8, blur = 10, max_zoom=12, gradient=None).add_to(fonxmap)
fonxmap
#fonxmap.save('Bronx_Injuries_Heatmap.html')

Injuries and fatalities by month due to vehicle crashes, from 2012 to 2025, for all of New York.


In [35]:
#press play button to see it go through the months
injury_df = new_data
injury_df['CRASH DATE'] = pd.to_datetime(injury_df['CRASH DATE'], format='%m/%d/%Y')


injury_data = injury_df[(injury_df['NUMBER OF PERSONS INJURED'] > 0) & (injury_df['NUMBER OF PERSONS KILLED'] == 0)]
injury_data['MONTH'] = injury_data['CRASH DATE'].dt.to_period('M')


inj_data_by_month = [
    injury_data[injury_data['MONTH'] == m][['LATITUDE', 'LONGITUDE']].values.tolist()
    for m in sorted(injury_data['MONTH'].unique())
]

ijm_time = fm.Map(location=nyc_center, zoom_start=11, tiles='CartoDB positron')
HeatMapWithTime(
    inj_data_by_month,
    radius=8,
    auto_play=True,
    max_opacity=0.8,
    display_index=True,
).add_to(ijm_time)
ijm_time
#ijm_time.save("Injuries_Heatmap_Time.html")

Output hidden; open in https://colab.research.google.com to view.

Side by side comparison New York, car crash outcomes: Injuries vs Fatalities

In [36]:
injury_ppl = injury_df[injury_df['NUMBER OF PERSONS INJURED'] > 0]
fatal_ppl = injury_df[injury_df['NUMBER OF PERSONS KILLED'] > 0]

print(f"Injury crashes: {len(injury_ppl):,}")
print(f"Fatal crashes: {len(fatal_ppl):,}")


nyc_center = [40.7128, -74.0060]

fig = Figure(width='100%', height='500px')


m1 = fm.Map(location=nyc_center, zoom_start=11, tiles='CartoDB positron')
injury_num = injury_ppl[['LATITUDE', 'LONGITUDE']].values.tolist()
HeatMap(injury_num, radius=8, blur=10, max_zoom=12, name="Injury Crashes").add_to(m1)

# Add a title
title_html = '''
             <h3 align="center" style="font-size:16px"><b>NYC Vehicle Crashes Causing Injuries</b></h3>
             '''
m1.get_root().html.add_child(fm.Element(title_html))

# --- Right map: Fatal crashes ---
m2 = fm.Map(location=nyc_center, zoom_start=11, tiles='CartoDB dark_matter')
fatal_num = fatal_ppl[['LATITUDE', 'LONGITUDE']].values.tolist()
HeatMap(fatal_num, radius=10, blur=15, max_zoom=12, name="Fatal Crashes", gradient={0.4: 'blue', 0.65: 'lime', 1: 'red'}).add_to(m2)

title_html2 = '''
             <h3 align="center" style="font-size:16px"><b>NYC Vehicle Crashes Causing Fatalities</b></h3>
             '''
m2.get_root().html.add_child(fm.Element(title_html2))


fig.add_child(m1)
fig.add_child(m2)


m1.save("nyc_injury_crash_heatmap.html")
m2.save("nyc_fatal_crash_heatmap.html")


dual_destiny = DualMap(location=nyc_center,  zoom_start=11)

HeatMap(injury_num, radius=8, blur=10, max_zoom=12, name="Injury Crashes").add_to(dual_destiny.m1)

HeatMap(fatal_num,radius=8, blur=10, max_zoom=12, name="Fatal Crashes").add_to(dual_destiny.m2)
dual_destiny
#dual_destiny.save("dual_destiny.html")


Output hidden; open in https://colab.research.google.com to view.

In [37]:
import geopandas as gpd
nyc_zip_geo = gpd.read_file("/content/drive/My Drive/nyc_zip_geo.geojson")
nyc_zip_geo.head()
nyc_zip_geo.shape

(262, 12)

https://www.kaggle.com/datasets/ashioyajotham/nyc-geojson-file
used this geojson dataset for the heatmaps below

In [40]:


#Injuries in Chloropleth - cleaner? by zipcode
#blacked out areas have 0
tort_data = new_data[new_data['NUMBER OF PERSONS INJURED'] > 0]
injm = fm.Map(location=[40.7128, -74.0060], zoom_start=12)
fm.Choropleth(
    geo_data=nyc_zip_geo,
    name='Vehicle Crashes',
    data=tort_data,
    columns=['ZIP CODE', 'NUMBER OF PERSONS INJURED'],
    key_on='feature.properties.postalCode',  # or 'feature.properties.ZIPCODE' depending on the geojson field
    fill_color='YlOrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Number of Persons Injured in Vehicle Crashes'
).add_to(injm)
fm.features.GeoJson(
    nyc_zip_geo,
    name='ZipCode',
    style_function=lambda x: {'fillColor': 'transparent', 'color': 'transparent'},
    tooltip=fm.features.GeoJsonTooltip(
        fields=['postalCode'],  # must match your GeoJSON properties
        aliases=['ZIP Code:'],
        localize=False
    )
).add_to(injm)
injm
#injm.save('Injuries_by_zipcode.html')

In [41]:
#Fatalities in Chloropleth - cleaner? by zipcode
#blacked out areas have 0
mort_data = new_data[new_data['NUMBER OF PERSONS KILLED'] > 0]
kilm = fm.Map(location=[40.7128, -74.0060], zoom_start=12)
fm.Choropleth(
    geo_data=nyc_zip_geo,
    name='Vehicle Crashes',
    data=mort_data,
    columns=['ZIP CODE', 'NUMBER OF PERSONS KILLED'],
    key_on='feature.properties.postalCode',  # or 'feature.properties.ZIPCODE' depending on the geojson field
    fill_color='YlOrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Number of Persons Killed in Vehicle Crashes'
).add_to(kilm)
fm.features.GeoJson(
    nyc_zip_geo,
    name='ZipCode',
    style_function=lambda x: {'fillColor': 'transparent', 'color': 'transparent'},
    tooltip=fm.features.GeoJsonTooltip(
        fields=['postalCode'],  # must match your GeoJSON properties
        aliases=['ZIP Code:'],
        localize=False
    )
).add_to(kilm)
kilm
#kilm.save('Fatalities_by_zipcode.html')